# Capstone assignment

Importing relevant libraries

In [1]:
import pandas as pd
import requests

import numpy as np # library to handle data in a vectorized manner

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe


# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
#=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.18.1               |             py_0          51 KB  conda-forge
    openssl-1.0.2p             |    h14c3975_1002         3.1 MB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.2 MB

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0         conda-forge
    geopy:         1.18.1-py_0       conda-forge

The following packages will be UPDATED:

    openssl:       1.0.2p-h470a237_1 conda-forge --> 1.0.2p-h14c3975_1002 conda-forge


geopy-1.18.1         | 51 KB     | ##################################### | 100% 


##### Downloading New York data, same from previous assignment in course

In [2]:
!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


##### Load and explore data

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

##### Look at the data

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

##### Retrieve the relevant data in the *features* key, which is basically a list of the neighborhoods.

In [5]:
neighborhoods_data = newyork_data['features']

##### Tranform the data into a pandas dataframe
###### Start with creating an empty dataframe

In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

##### Loop through the data and fill the dataframe one row at a time.

In [7]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [8]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

#### Segment and cluster only the neighborhoods in Manhattan. So let's slice the original dataframe and create a new dataframe of the Manhattan data.

In [9]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

##### Get geographical coordinates of Manhattan

In [10]:
address = 'Manhattan, New York City'

geolocator = Nominatim(user_agent="capstoneProject")
location = geolocator.geocode(address, timeout=60, exactly_one=True)
latitude = location.latitude
longitude = location.longitude
print('The decimal coordinates of Manhattan are {}, {}.'.format(latitude, longitude))

The decimal coordinates of Manhattan are 40.7900869, -73.9598295.


#### Copy the dataframe to restore work easily

In [11]:
df_man = manhattan_data.copy()
df_man

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

#### Create a map of Manhattan

In [12]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, local in zip(df_man['Latitude'], df_man['Longitude'], df_man['Neighborhood']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_manhattan)  
    
map_manhattan

#### Function to repeat the exploring process to all the neighborhoods in Manhattan

In [32]:
import urllib
def getNearbyVenues(names, latitudes, longitudes, radius=5000, limit=500, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, limit)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        print(results)
        print(nearby_venues)

    return(nearby_venues)

##### Define Foursquare Credentials and Version

In [33]:
CLIENT_ID = 'FMR3OGXQDOSLEBPX30G4YWRNANUJWHIWWIK0A0ARKJDRCT5Y'
CLIENT_SECRET = 'H5US3SIKGAL0JNQSMVG0G3H4BCNIVTRG3UWFNVRR1DSXHIER'
VERSION = '20180605'

##### Retrieve healthy food stores on Manhattan

In [20]:
# Use category id 50aa9e744b90af0d42d5de0e from Foursquare to only get healthy food stores
man_health = getNearbyVenues(names=df_man['Neighborhood'], latitudes=df_man['Latitude'], longitudes=df_man['Longitude'], 
                             radius=1000, limit=500, categoryIds='50aa9e744b90af0d42d5de0e')
man_health.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551              -73.910660   
1  Marble Hill              40.876551              -73.910660   
2    Chinatown              40.715618              -73.994279   
3    Chinatown              40.715618              -73.994279   
4    Chinatown              40.715618              -73.994279   

                Venue  Venue Latitude  Venue Longitude     Venue Category  
0      Vitamin Shoppe       40.877160       -73.905632    Supplement Shop  
1                 GNC       40.879760       -73.904484    Supplement Shop  
2  Wing Fung Hong Ltd       40.714108       -73.994920  Health Food Store  
3  Whole Foods Market       40.723875       -73.991976      Grocery Store  
4                 GNC       40.718647       -73.995652    Supplement Shop

In [21]:
man_health.shape

(361, 7)

##### Function to add markers for given venues to map

In [22]:
def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Neighborhood'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

##### Map health food stores on Manhattan

In [23]:
map_man_health = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(man_health, 'red', map_man_health)
map_man_health

##### Find gyms on Manhattan and map them

In [29]:
# Use category id 4bf58dd8d48988d175941735 from Foursquare to only get gym/fitness centres
man_gym = getNearbyVenues(names=df_man['Neighborhood'], latitudes=df_man['Latitude'], longitudes=df_man['Longitude'], radius=1000, 
                          limit=50, categoryIds='4bf58dd8d48988d175941735')
man_gym.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                                           Venue  Venue Latitude  \
0                                   Bronx Boxing       40.875671   
1                                 La Palestra 99       40.873919   
2               Astral Fitness & Wellness Center       40.876705   
3  3210 Riverdale Avenue - Wellness Center & Gym       40.882746   
4                                 Planet Fitness       40.874088   

   Venue Longitude        Venue Category  
0       -73.908355            Boxing Gym  
1       -73.917065                   Gym  
2       -73.906372                   Gym  
3       -73.907625                   Gym  
4       -73.909137  Gym / Fitness Center

In [30]:
man_gym.shape

(1885, 7)

In [31]:
map_man_gym = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(man_gym, 'green', map_man_gym)
map_man_gym

##### Find metro stations on Manhattan

In [34]:
# Use category id 4bf58dd8d48988d1fd931735 from Foursquare to only get metro stations
man_met = getNearbyVenues(names=df_man['Neighborhood'], latitudes=df_man['Latitude'], longitudes=df_man['Longitude'], radius=1000, limit=500, categoryIds='4bf58dd8d48988d1fd931735')
man_met.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                                   Venue  Venue Latitude  Venue Longitude  \
0  MTA Subway - 225th St/Marble Hill (1)       40.874486       -73.909589   
1              MTA Subway - 231st St (1)       40.878825       -73.904930   
2              MTA Subway - 215th St (1)       40.869417       -73.915396   
3      215th Street Subway Stop (1 Line)       40.869881       -73.915858   
4                                 Mac #3       40.867435       -73.909081   

  Venue Category  
0  Metro Station  
1  Metro Station  
2  Metro Station  
3  Metro Station  
4  Metro Station

In [35]:
man_met.shape

(497, 7)

In [36]:
map_man_met = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(man_met, 'gold', map_man_met)
map_man_met

##### Find offices on Manhattan

In [37]:
# Use category id 4bf58dd8d48988d124941735 from Foursquare to only get offices
man_off = getNearbyVenues(names=df_man['Neighborhood'], latitudes=df_man['Latitude'], longitudes=df_man['Longitude'], radius=1000, limit=500, categoryIds='4bf58dd8d48988d124941735')
man_off.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                                              Venue  Venue Latitude  \
0                                     Bettter Taxes       40.876311   
1                     River Plaza Management Office       40.874742   
2                                   All Over Travel       40.874414   
3                                       The Dungeon       40.869243   
4  Security Guards - National Security Service, LLC       40.877849   

   Venue Longitude   Venue Category  
0       -73.913145  Coworking Space  
1       -73.909925           Office  
2       -73.911446           Office  
3       -73.916442  Coworking Space  
4       -73.910064           Office

In [38]:
man_off.shape

(1922, 7)

In [39]:
map_man_off = folium.Map(location=[latitude, longitude], zoom_start=12)
addToMap(man_off, 'fuchsia', map_man_off)
map_man_off

##### Find Residential Building (Apartment / Condo) on Manhattan

In [40]:
# Use category id 4d954b06a243a5684965b473 from Foursquare to only get Residential Building (Apartment / Condo
man_res = getNearbyVenues(names=df_man['Neighborhood'], latitudes=df_man['Latitude'], longitudes=df_man['Longitude'], radius=1000, categoryIds='4d954b06a243a5684965b473')
man_res.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                   Venue  Venue Latitude  Venue Longitude  \
0         Promenade Apts       40.875424       -73.913576   
1              98 P.T.E.       40.871177       -73.915525   
2      2390 Palisade AVE       40.879570       -73.920777   
3  The Century Riverdale       40.878855       -73.914762   
4      West 230th Street       40.875714       -73.903130   

                             Venue Category  
0  Residential Building (Apartment / Condo)  
1  Residential Building (Apartment / Condo)  
2  Residential Building (Apartment / Condo)  
3  Residential Building (Apartment / Condo)  
4  Residential Building (Apartment / Condo)

In [41]:
man_res.shape

(1998, 7)

##### Function to add columns

In [42]:
def addColumn(startDf, columnTitle, dataDf):
    grouped = dataDf.groupby('Neighborhood').count()
    
    for n in startDf['Neighborhood']:
        try:
            startDf.loc[startDf['Neighborhood'] == n,columnTitle] = grouped.loc[n, 'Venue']
        except:
            startDf.loc[startDf['Neighborhood'] == n,columnTitle] = 0

##### Copy of dataframe and adding columns

In [43]:
df_data = df_man.copy()
#df_data.rename(columns={'Localidades':'Localidad'}, inplace=True)
addColumn(df_data, 'Health food stores', man_health)
addColumn(df_data, 'Gym', man_gym)
addColumn(df_data, 'Metro stations', man_met)
addColumn(df_data, 'Offices', man_off)
addColumn(df_data, 'Residential building', man_res)
df_data

Borough         Neighborhood   Latitude  Longitude  Health food stores  \
0   Manhattan          Marble Hill  40.876551 -73.910660                 2.0   
1   Manhattan            Chinatown  40.715618 -73.994279                 9.0   
2   Manhattan   Washington Heights  40.851903 -73.936900                 1.0   
3   Manhattan               Inwood  40.867684 -73.921210                 3.0   
4   Manhattan     Hamilton Heights  40.823604 -73.949688                 2.0   
5   Manhattan       Manhattanville  40.816934 -73.957385                 1.0   
6   Manhattan       Central Harlem  40.815976 -73.943211                 3.0   
7   Manhattan          East Harlem  40.792249 -73.944182                 2.0   
8   Manhattan      Upper East Side  40.775639 -73.960508                 5.0   
9   Manhattan            Yorkville  40.775930 -73.947118                 4.0   
10  Manhattan           Lenox Hill  40.768113 -73.958860                 5.0   
11  Manhattan     Roosevelt Island  40.762160 -73.949168                 3.0   
12  Manhattan      Upper West Side  40.787658 -73.977059                 5.0   
13  Manhattan       Lincoln Square  40.773529 -73.985338                10.0   
14  Manhattan              Clinton  40.759101 -73.996119                17.0   
15  Manhattan              Midtown  40.754691 -73.981669                27.0   
16  Manhattan          Murray Hill  40.748303 -73.978332                21.0   
17  Manhattan              Chelsea  40.744035 -74.003116                12.0   
18  Manhattan    Greenwich Village  40.726933 -73.999914                15.0   
19  Manhattan         East Village  40.727847 -73.982226                11.0   
20  Manhattan      Lower East Side  40.717807 -73.980890                 4.0   
21  Manhattan              Tribeca  40.721522 -74.010683                11.0   
22  Manhattan         Little Italy  40.719324 -73.997305                13.0   
23  Manhattan                 Soho  40.722184 -74.000657                14.0   
24  Manhattan         West Village  40.734434 -74.006180                10.0   
25  Manhattan     Manhattan Valley  40.797307 -73.964286                 5.0   
26  Manhattan  Morningside Heights  40.808000 -73.963896                 2.0   
27  Manhattan             Gramercy  40.737210 -73.981376                17.0   
28  Manhattan    Battery Park City  40.711932 -74.016869                 5.0   
29  Manhattan   Financial District  40.707107 -74.010665                 5.0   
30  Manhattan        Carnegie Hill  40.782683 -73.953256                 4.0   
31  Manhattan                 Noho  40.723259 -73.988434                11.0   
32  Manhattan         Civic Center  40.715229 -74.005415                10.0   
33  Manhattan        Midtown South  40.748510 -73.988713                24.0   
34  Manhattan         Sutton Place  40.760280 -73.963556                 8.0   
35  Manhattan           Turtle Bay  40.752042 -73.967708                10.0   
36  Manhattan           Tudor City  40.746917 -73.971219                12.0   
37  Manhattan      Stuyvesant Town  40.731000 -73.974052                 3.0   
38  Manhattan             Flatiron  40.739673 -73.990947                25.0   
39  Manhattan         Hudson Yards  40.756658 -74.000111                10.0   

     Gym  Metro stations  Offices  Residential building  
0   26.0             5.0     39.0                  48.0  
1   50.0            15.0     50.0                  50.0  
2   22.0             5.0     37.0                  50.0  
3   13.0            11.0     38.0                  50.0  
4   39.0             6.0     45.0                  50.0  
5   46.0             5.0     46.0                  50.0  
6   48.0            14.0     49.0                  50.0  
7   50.0             7.0     44.0                  50.0  
8   50.0             5.0     50.0                  50.0  
9   50.0             3.0     49.0                  50.0  
10  50.0             5.0     50.0                  50.0  
11  50.0             3.0     

In [44]:
# negative weight, because I want to open a healthy food store and therefore want to avoid competition as much as possible
weight_health = -1

# positive weight, because people prefer when communiting by metro to have the store close
weight_met = 1

# positive weight, because people exercisng at the gym want to combine training with health food
weight_gym = 1.5

# positive weight, because people working at offices want "fast food" and healthy
weight_off = 1.2

# positive weight because resedentials want to be able to eat healthy
weight_res = 2

In [45]:
df_weighted = df_data[['Neighborhood']].copy()

In [48]:
df_weighted['Score'] = df_data['Health food stores'] * weight_health + df_data['Gym'] * weight_gym + df_data['Metro stations'] * weight_met + df_data['Offices'] * weight_off + df_data['Residential building'] * weight_res
df_weighted = df_weighted.sort_values(by=['Score'], ascending=False)
df_weighted

Neighborhood  Score
29   Financial District  252.0
28    Battery Park City  251.0
32         Civic Center  250.0
22         Little Italy  248.0
21              Tribeca  246.0
31                 Noho  244.0
18    Greenwich Village  243.0
6        Central Harlem  241.8
1             Chinatown  241.0
23                 Soho  241.0
17              Chelsea  238.0
20      Lower East Side  238.0
24         West Village  237.0
34         Sutton Place  237.0
38             Flatiron  237.0
30        Carnegie Hill  235.8
8       Upper East Side  235.0
13       Lincoln Square  235.0
10           Lenox Hill  235.0
39         Hudson Yards  235.0
19         East Village  235.0
33        Midtown South  234.0
14              Clinton  233.0
15              Midtown  233.0
9             Yorkville  232.8
7           East Harlem  232.8
11     Roosevelt Island  232.6
27             Gramercy  231.0
35           Turtle Bay  231.0
12      Upper West Side  229.8
26  Morningside Heights  229.2
36           Tudor City  229.0
5        Manhattanville  228.2
16          Murray Hill  227.0
37      Stuyvesant Town  225.9
25     Manhattan Valley  225.2
4      Hamilton Heights  216.5
0           Marble Hill  184.8
2    Washington Heights  181.4
3                Inwood  173.1

### The best neighborhood to open a health food store in on Manhattan

In [51]:
map_man_result = folium.Map(location=[latitude, longitude], zoom_start=11)

man_win = df_man[df_man['Neighborhood'] == 'Financial District']

for lat, lng, local in zip(man_win['Latitude'], man_win['Longitude'], man_win['Neighborhood']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(map_man_result) 

addToMap(man_health[man_health['Neighborhood'] == 'Financial District'], 'red', map_man_result)
addToMap(man_gym[man_gym['Neighborhood'] == 'Financial District'], 'green', map_man_result)
addToMap(man_met[man_met['Neighborhood'] == 'Financial District'], 'gold', map_man_result)
addToMap(man_off[man_off['Neighborhood'] == 'Financial District'], 'fuchsia', map_man_result)
addToMap(man_res[man_res['Neighborhood'] == 'Financial District'], 'orange', map_man_result)

map_man_result

### Financial district is the best option for opening a healthy food store